In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import lit
spark.sparkContext.setLogLevel('info') 

In [0]:
spark = SparkSession.builder \
    .config('spark.jars.packages', 'io.github.marquezproject:marquez-spark:0.15.2') \
    .config('spark.extraListeners', 'marquez.spark.agent.SparkListener') \
    .config('openlineage.url', 'https://domain.com') \
    .config('openlineage.namespace', 'my-namespace') \
    .getOrCreate()

In [0]:
#Supress success
spark.sparkContext._jsc.hadoopConfiguration().set('mapreduce.fileoutputcommitter.marksuccessfuljobs', 'false')
spark.sparkContext._jsc.hadoopConfiguration().set('parquet.summary.metadata.level', 'NONE')
df_source_trip = spark.read \
    .option('header', True) \
    .option('delimiter', ',') \
    .csv('/FileStore/tables/2593269.csv') \
    .createOrReplaceTempView('source_trip')

In [0]:
spark.conf

Out[5]: <pyspark.sql.conf.RuntimeConfig at 0x7ff330863210>

In [0]:
display(df_source_trip)

In [0]:
df_drivers = spark.table('source_trip') \
    .select('name') \
    .distinct() \
    .createOrReplaceTempView('src_driver')
df = spark.sql(
    """
    SELECT d.*, t.*
      FROM source_trip t, src_driver d
    """
)


In [0]:
df.coalesce(1) \
    .drop('NAME')\
    .write.mode('overwrite') \
    .option('path', '/FileStore/tables/2593269_target.csv') \
    .saveAsTable('trip')

In [0]:
display(df)

In [0]:
import requests

In [0]:
url = "https://openlineage.alationcatalog.com/api/v1"

In [0]:
data = {
        "eventType": "START",
        "eventTime": "2020-12-28T19:52:00.001+10:00",
        "run": {
          "runId": "d46e465b-d358-4d32-83d4-df660ff614dd"
        },
        "job": {
          "namespace": "databricks_integration",
          "name": "my-job1"
        },
        "inputs": [{
          "namespace": "databricks_integration",
          "name": "my-input1"
        }],  
        "producer": "https://github.com/OpenLineage/OpenLineage/blob/v1-0-0/client"
      }
res = requests.post(url+"/lineage/", json=data)

In [0]:
res

In [0]:
data = {
        "eventType": "COMPLETE",
        "eventTime": "2020-12-28T20:52:00.001+10:00",
        "run": {
          "runId": "d46e465b-d358-4d32-83d4-df660ff614dd"
        },
        "job": {
          "namespace": "databricks_integration",
          "name": "my-job1"
        },
        "outputs": [{
          "namespace": "databricks_integration",
          "name": "my-output1",
          "facets": {
            "schema": {
              "_producer": "https://github.com/OpenLineage/OpenLineage/blob/v1-0-0/client",
              "_schemaURL": "https://github.com/OpenLineage/OpenLineage/blob/v1-0-0/spec/OpenLineage.json#/definitions/SchemaDatasetFacet",
              "fields": [
                { "name": "a", "type": "VARCHAR"},
                { "name": "b", "type": "VARCHAR"}
              ]
            }
          }
        }],     
        "producer": "https://github.com/OpenLineage/OpenLineage/blob/v1-0-0/client"
      }
res = requests.post(url+"/lineage/", json=data)

In [0]:
res.text